In [1]:
#default_exp content_based 

In [2]:
#export 

import scipy
import pandas as pd
import numpy as np


from sklearn import compose, feature_extraction, metrics
from functools import reduce, partial
import attr
from typing import Union
import umap
import altair


from game_recommender import steam_data

In [3]:
%cd ..

/home/kuba/Projects/game_recommender


In [4]:
??steam_data.load_steam_df

Signature:
steam_data.load_steam_df(
    steam_games_metadata_path='data/steam_games_metadata/steam_games.csv',
)
Docstring: <no docstring>
Source:   
def load_steam_df(steam_games_metadata_path=STEAM_GAME_METADATA_PATH):
    return clean_steam_df(pd.read_csv(steam_games_metadata_path))
File:      ~/Projects/game_recommender/game_recommender/steam_data.py
Type:      function


In [5]:
steam_df = steam_data.load_steam_df() 

In [6]:
chosen_games_substring = 's.t.a.l.k'

In [7]:
chosen_games_df = steam_data.get_games_by_name(steam_df, chosen_games_substring) 

In [8]:
chosen_games_df['name']

376     s.t.a.l.k.e.r. shadow of chernobyl
1276        s.t.a.l.k.e.r. call of pripyat
7253              s.t.a.l.k.e.r. clear sky
Name: name, dtype: object

In [9]:
chosen_games_df.iloc[0]['popular_tags']

'atmospheric,post-apocalyptic,open world,fps,survival,masterpiece,action,rpg,survival horror,shooter,horror,first-person,singleplayer,classic,based on a novel,moddable,adventure,sci-fi,inventory management,difficult'

In [10]:
chosen_games_df.iloc[0]['game_details']

'single-player,multi-player'

In [11]:
chosen_games_df.iloc[0]['genre']

'action,rpg'

In [12]:
chosen_games_df['game_description'].iloc[0]

" About This Game In 1986, the world's worst nuclear disaster occurred at the Chernobyl Nuclear Power Plant. Soviet authorities established an 'Exclusion Zone' around, but a second explosion hit the reactor in 2006, creating The Zone as we know it – dangerous place, filled with mutated creatures, deadly radiation, and a strange, anomalous energy. The Zone was cordoned off by the military, who would shoot on sight anyone foolish enough to get inside.  Year 2012. The Zone is still a dangerous place and a threat to all mankind. Mercenaries, bounty hunters and explorers ventured further and further into the heart of the Zone driven by reports of strange 'artifacts' imbued with anomalous energy. To sell them on the black market or trying to find the 'truth' behind the Zone. Whatever their motivation, over time these individuals - Scavengers, Trespassers, Adventurers, Loners, Killers, Explorers and Robbers - have become known as S.T.A.L.K.E.R.s.  You will have to find your own way to survive

In [13]:
chosen_games_df['popular_tags'].iloc[0]

'atmospheric,post-apocalyptic,open world,fps,survival,masterpiece,action,rpg,survival horror,shooter,horror,first-person,singleplayer,classic,based on a novel,moddable,adventure,sci-fi,inventory management,difficult'

In [14]:
game_descriptions = steam_df['game_description']

# Finding games with similar descriptions

In [15]:
from collections import defaultdict

In [16]:
#export

def split_by_comma_tokenizer(text):
    return text.split(',') 


def _regroup_weights(weights, column_groups):
    assert len(weights) == len(column_groups), 'specify weight for each column group'
    return {
        col: weight / len(col_group)
        for (weight, col_group) in zip(weights, column_groups)
        for col in col_group
    }


def make_df_column_vectorizer(
        column_groups,
        vectorizer_classes=feature_extraction.text.TfidfVectorizer,
        weights=None,
        tokenizers=None
    ):
    if type(vectorizer_classes) is not list:
        vectorizer_classes = [vectorizer_classes for __ in range(len(column_groups))]
    if tokenizers is None:
        tokenizers = [None for __ in range(len(column_groups))]
    vectorizers = [vectorizer_class(tokenizer=tokenizer) for (vectorizer_class, grp, tokenizer) in zip(vectorizer_classes, column_groups, tokenizers)] 
    if type(weights) is list:
        weights = _regroup_weights(weights, column_groups)
    
    return compose.ColumnTransformer(
        [
            (col + '_tfidf', vectorizer, col)
            for columns, vectorizer in zip(column_groups, vectorizers)
            for col in columns
        ],
        transformer_weights=weights
    )

In [17]:
vectorizer = make_df_column_vectorizer([
        ['popular_tags'],
        ['game_description', 'desc_snippet'],
    ],
    vectorizer_classes=partial(
            feature_extraction.text.TfidfVectorizer,
            binary=True,
            min_df=5
    ),
    tokenizers=[split_by_comma_tokenizer, None]
)

steam_metadata_vectors = vectorizer.fit_transform(steam_df)

In [18]:
steam_df.shape

(24210, 21)

In [19]:
steam_metadata_vectors.shape

(24210, 31455)

In [20]:
x = None
if 1 is not None:
    print(x)

None


In [21]:
#export

@attr.s
class SimilaritySearcher:
    
    df: pd.DataFrame = attr.ib()
    vectors: Union[scipy.sparse.csr.csr_matrix, np.array] = attr.ib()
    similarity = attr.ib(default=metrics.pairwise.cosine_similarity)
    name_col = attr.ib(default='name')
    
    def find_similar(
            self,
            chosen_items=None,
            chosen_vectors=None,
            n_similar=20):
        def get_names_from_indices(indices):
            return self.df[self.name_col].iloc[indices].values
    
        assert chosen_items is not None or chosen_vectors is not None
        if not chosen_items is None:
            idxs = self.df[self.df[self.name_col].isin(chosen_items)].index
            chosen_vectors = self.vectors[idxs]
        else:
            chosen_items = list(map(str, range(chosen_vectors.shape[0])))
        mean_vector = chosen_vectors.mean(axis=0)
        similarities = self.similarity(chosen_vectors, self.vectors)
        similarity_sorted_indices = similarities.argsort(axis=1)[:,::-1]
        similarities_sorted = np.array([similarities[i, similarity_sorted_indices[i]] for i in range(len(chosen_items))])
        mean_similarity = self.similarity(mean_vector.reshape(1,-1), self.vectors)
        mean_similarity_sorted_indices = mean_similarity.argsort(axis=1)[:,::-1]
        mean_similarities_sorted = mean_similarity[0,mean_similarity_sorted_indices.reshape(-1)]

        mean_similar = get_names_from_indices(mean_similarity_sorted_indices[0][:n_similar])
        game_names = {}
        similarities = {}
        
        for (i, name) in enumerate(chosen_items):
            game_names[str(name)] = ( 
                    get_names_from_indices(
                        similarity_sorted_indices[i][1:n_similar+1]
                    )
            )
            similarities[str(name) + '_similarities'] = similarities_sorted[i][:n_similar]

        game_names['mean'] = mean_similar
        similarities['mean_similarity'] = mean_similarities_sorted[1:n_similar+1] 
        return pd.DataFrame(game_names), pd.DataFrame(similarities)

In [22]:
#export

def make_stacked_results_df(game_names, similarities):
    df = pd.concat([game_names, similarities], axis=1)
    return df.reindex(sorted(df.columns), axis=1)

In [23]:
metadata_df = steam_df
n_similar=20
metadata_vectors = steam_metadata_vectors


In [24]:
from sklearn import decomposition

n_components = 250


tsvd = decomposition.TruncatedSVD(n_components=n_components)
nmf = decomposition.NMF(n_components=n_components, solver='mu')

In [25]:
%%time
steam_metadata_reduced_vectors = tsvd.fit_transform(steam_metadata_vectors)

CPU times: user 33.1 s, sys: 14.6 s, total: 47.7 s
Wall time: 11.4 s


In [26]:
import cuml

In [27]:
#export

def get_similar_game_names_from_results(results):
    return set(results.values.reshape(-1))


In [29]:
similarity_searcher = SimilaritySearcher(steam_df, steam_metadata_reduced_vectors)

# Searching by SVD reduced data

In [30]:
make_stacked_results_df(*similarity_searcher.find_similar(chosen_games_df['name']))

mean  mean_similarity  \
0             s.t.a.l.k.e.r. clear sky         0.948423   
1       s.t.a.l.k.e.r. call of pripyat         0.922222   
2   s.t.a.l.k.e.r. shadow of chernobyl         0.730379   
3               metro last light redux         0.712243   
4                     metro 2033 redux         0.669598   
5               unreal 2 the awakening         0.665340   
6       time ramesside a new reckoning         0.659244   
7                                zombi         0.658836   
8                            fallout 3         0.657250   
9                    fallout new vegas         0.656331   
10                             far cry         0.644779   
11                              doom 3         0.642342   
12                  doom 3 bfg edition         0.640492   
13      nosferatu the wrath of malachi         0.639189   
14                         dead effect         0.637243   
15                        metro exodus         0.636847   
16                                dayz         0.633621   
17                    arizona sunshine         0.630060   
18             half life 2 episode two         0.628091   
19  fallout 3 game of the year edition         0.627801   

        s.t.a.l.k.e.r. call of pripyat  \
0             s.t.a.l.k.e.r. clear sky   
1   s.t.a.l.k.e.r. shadow of chernobyl   
2               metro last light redux   
3                     metro 2033 redux   
4                              far cry   
5                                 dayz   
6               unreal 2 the awakening   
7                   doom 3 bfg edition   
8                    fallout new vegas   
9                            fallout 3   
10      time ramesside a new reckoning   
11                               zombi   
12                 shadows of kurgansk   
13                              doom 3   
14             half life 2 episode two   
15                     estranged act i   
16  fallout 3 game of the year edition   
17                      state of decay   
18                            unturned   
19                    arizona sunshine   

    s.t.a.l.k.e.r. call of pripyat_similarities  \
0                                      1.000000   
1                                      0.898894   
2                                      0.784304   
3                                      0.686985   
4                                      0.684831   
5                                      0.675177   
6                                      0.674081   
7                                      0.654021   
8                                      0.652543   
9                                      0.645686   
10                                     0.644753   
11                                     0.642798   
12                                     0.641665   
13                                     0.639811   
14                                     0.638235   
15                                     0.629812   
16                                     0.628723   
17                                     0.621411   
18                                     0.620507   
19                                     0.618390   

              s.t.a.l.k.e.r. clear sky  s.t.a.l.k.e.r. clear sky_similarities  \
0       s.t.a.l.k.e.r. call of pripyat                               1.000000   
1   s.t.a.l.k.e.r. shadow of chernobyl                               0.898894   
2               metro last light redux                               0.837184   
3                     metro 2033 redux                               0.688826   
4       time ramesside a new reckoning                               0.680271   
5                                zombi                               0.672780   
6               unreal 2 the awakening                               0.671571   
7                   doom 3 bfg edition                               0.650290   
8                               doom 3                               0.641652   
9                          de

# Searching by NMF reduced data

In [31]:
#%%time
#steam_metadata_nmf_vectors = nmf.fit_transform(steam_metadata_vectors)

In [32]:
#similar_games(chosen_games_df, steam_df, steam_metadata_nmf_vectors)

In [33]:
# Recommending

In [34]:
#export


@attr.s
class ContentBasedRecommender:
    
    similarity_searcher: SimilaritySearcher = attr.ib()
        
    def recommend_similar_games(self, rated_games, ratings, n_recommended, n_similar=20):
        similar_games, similarities = self.similarity_searcher.find_similar(rated_games, n_similar=n_similar)
        mean_similar_games = similar_games.pop('mean')
        mean_similarities = similarities.pop('mean_similarity')
        
        predicted_ratings = ratings * similarities / similarities.max()
        predicted_ratings_flat = pd.concat([predicted_ratings[col] for col in predicted_ratings.columns])
        similar_games_flat = pd.concat([similar_games[col] for col in similar_games.columns])
        # TODO: is this best way to handle duplicates?
        pred_df = pd.DataFrame({
            'game': similar_games_flat,
            'rating ': predicted_ratings_flat
        }).groupby('game').agg('mean')
        predicted_ratings_flat = pred_df.iloc[:,0].values
        similar_games_flat = pred_df.index.values
        
        best_rated_indices = np.argsort(predicted_ratings_flat)[::-1][:n_recommended]
        best_ratings = predicted_ratings_flat[best_rated_indices]
        best_rated_games = similar_games_flat[best_rated_indices]
        return best_rated_games, best_ratings
        
    def recommend_mean_similar_games(self, rated_games, ratings, n_recommended, n_similar=20):
        similar_games, similarities = self.similarity_searcher.find_similar(rated_games_df, n_similar=n_similar)
        mean_similar_games = similar_games.pop('mean')
        mean_similarities = similarities.pop('mean_similarity')
        return mean_similar_games, mean_similarities

In [35]:
ratings = [4, 5, 6]
rated_games = chosen_games_df['name']

In [36]:
content_recommender = ContentBasedRecommender(similarity_searcher)
recommended_games, ratings = content_recommender.recommend_similar_games(rated_games, ratings, 20)

In [37]:
recommended_games

array(['s.t.a.l.k.e.r. shadow of chernobyl',
       's.t.a.l.k.e.r. call of pripyat', 's.t.a.l.k.e.r. clear sky',
       'metro last light redux', 'dead effect', 'synergy', 'zombi',
       'far cry', 'doom 3 bfg edition', 'doom 3', 'dayz',
       'half life 2 episode two', 'metro 2033 redux', 'estranged act i',
       'arizona sunshine', 'unreal 2 the awakening',
       'shadows of kurgansk', 'time ramesside a new reckoning',
       'nosferatu the wrath of malachi', 'fallout new vegas'],
      dtype=object)

# Visualizing similar games with UMAP

In [38]:

umapper = umap.UMAP(
    random_state=0,
    n_neighbors=10,
    n_components=2,
    metric='cosine')
viz_data = umapper.fit_transform(steam_metadata_reduced_vectors)


alt.LayerChart(...)

In [40]:
viz_df = pd.DataFrame({
    'X': viz_data[:,0],
    'Y': viz_data[:,1],
    'name': steam_df['name'],
    'is_similar': steam_df['name'].isin(recommended_games)
})


altair.data_transformers.disable_max_rows()


similar_points_altair_scatterplot = (
    altair.Chart(viz_df[viz_df['is_similar']])
        .mark_circle(size=100, color='red', opacity=1.0)
        .encode(x='X', y='Y', tooltip=['name'])
        .interactive()
)

not_similar_points_altair_scatterplot = (
    altair.Chart(viz_df[~viz_df['is_similar']])
        .mark_circle(size=10, color='blue', opacity=0.1)
        .encode(x='X', y='Y', tooltip=['name'])
        .interactive()
)


similar_points_altair_scatterplot + not_similar_points_altair_scatterplot

alt.LayerChart(...)

In [39]:
# persisting stuff for streamlit
pd.DataFrame(viz_df).to_csv('data/steam_metadata_umap_vectors.csv.gz', index=False)
pd.DataFrame(steam_df).to_csv('data/steam_games.csv.gz', index=False)
pd.DataFrame(steam_metadata_reduced_vectors.astype('float16')).to_csv('data/steam_metadata_reduced_vectors.csv.gz', index=False)